In [1]:
import json
import os
import time
import random
from PIL import Image
import numpy as np
import matplotlib.pyplot as plt
from tqdm import tqdm
import shutil
import collections

import torch
import torch.nn as nn
import torch.backends.cudnn as cudnn
import torch.optim as optim
import torch.nn.functional as F
from torch.utils.data import DataLoader, Dataset
from torchvision import datasets
from torchvision import transforms
from torchvision import models
from torchsummary import summary

from model_pytorch import EfficientNet
from utils import Bar,Logger, AverageMeter, accuracy, mkdir_p, savefig
from warmup_scheduler import GradualWarmupScheduler
from sklearn.metrics import accuracy_score, roc_auc_score
from sklearn.model_selection import train_test_split

from scipy.ndimage.filters import gaussian_filter
import cv2

from PIL import ImageFile, ImageOps
ImageFile.LOAD_TRUNCATED_IMAGES = True

In [2]:
# GPU Device
gpu_id = 3
os.environ['CUDA_VISIBLE_DEVICES'] = str(gpu_id)
use_cuda = torch.cuda.is_available()
print("GPU device %d:" %(gpu_id), use_cuda)

GPU device 3: True


# Arguments

In [3]:
source_dir = '/media/data2/dataset/GAN_ImageData/PGGAN_128/'
target_dir = '/media/data2/dataset/GAN_ImageData/StyleGAN2_256/'

In [4]:
pretrained = './log/pggan/128/b0/aug/checkpoint.pth.tar'
resume = ''

In [5]:
# Model
model_name = 'efficientnet-b0' # b0-b7 scale

# Optimization
num_classes = 2
epochs = 40000
start_epoch = 0
train_batch = 100
test_batch = 200
lr = 0.04
schedule = [75, 175, 250]
momentum = 0.0
gamma = 0.1 # LR is multiplied by gamma on schedule

# CheckPoint
checkpoint = './log/pggan/128/b0/to_style2/aug_real' # dir
if not os.path.isdir(checkpoint):
    os.makedirs(checkpoint)
num_workers = 8

# Seed
manual_seed = 7
random.seed(manual_seed)
torch.cuda.manual_seed_all(manual_seed)

# Image
size = (128, 128)

# cutmix
cm_prob = 0.5
cm_prob_init = 0.99
cm_prob_low = 0.01
cm_beta = 1.0

# augmentation
blur_prob = 0.8
blog_sig = 0.5
jpg_prob = 0.8

best_acc = 0

# sp
sp_alpha = 0.1
sp_beta = 0.1
fc_name = '_fc.'

In [6]:
state = {}
state['num_classes'] = num_classes
state['epochs'] = epochs
state['start_epoch'] = start_epoch
state['train_batch'] = train_batch
state['test_batch'] = test_batch
state['lr'] = lr
state['schedule'] = schedule
state['momentum'] = momentum
state['gamma'] = gamma

In [7]:
def data_augment(img):
    img = np.array(img)

    if random.random() < blur_prob:
        sig = np.random.uniform(0.0, 3.0)
        gaussian_blur(img, sig)

    if random.random() < jpg_prob:
        qual = np.random.uniform(30.0, 100.0)
        img = cv2_jpg(img, qual)

    return Image.fromarray(img)


def gaussian_blur(img, sigma):
    gaussian_filter(img[:,:,0], output=img[:,:,0], sigma=sigma)
    gaussian_filter(img[:,:,1], output=img[:,:,1], sigma=sigma)
    gaussian_filter(img[:,:,2], output=img[:,:,2], sigma=sigma)


def cv2_jpg(img, compress_val):
    img_cv2 = img[:,:,::-1]
    encode_param = [int(cv2.IMWRITE_JPEG_QUALITY), compress_val]
    result, encimg = cv2.imencode('.jpg', img_cv2, encode_param)
    decimg = cv2.imdecode(encimg, 1)
    return decimg[:,:,::-1]

In [8]:
def rand_bbox(size, lam):
    W = size[2]
    H = size[3]
    cut_rat = np.sqrt(1. - lam)
    cut_w = np.int(W * cut_rat)
    cut_h = np.int(H * cut_rat)

    # uniform
    cx = np.random.randint(W)
    cy = np.random.randint(H)

    bbx1 = np.clip(cx - cut_w // 2, 0, W)
    bby1 = np.clip(cy - cut_h // 2, 0, H)
    bbx2 = np.clip(cx + cut_w // 2, 0, W)
    bby2 = np.clip(cy + cut_h // 2, 0, H)

    return bbx1, bby1, bbx2, bby2

# Dataset

In [9]:
train_dir = os.path.join(source_dir, '100_shot_style2')
val_target_dir = os.path.join(target_dir, 'validation')
val_source_dir = os.path.join(source_dir, 'validation')

train_aug = transforms.Compose([
    transforms.Lambda(lambda img: data_augment(img)),
    transforms.RandomCrop(size),
    transforms.RandomHorizontalFlip(),
    transforms.ToTensor(),
#     transforms.RandomErasing(p=0.3, scale=(0.02, 0.10), ratio=(0.3, 3.3), value=0, inplace=True),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])
val_aug = transforms.Compose([
    transforms.CenterCrop(size),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])

# pin_memory : cuda pin memeory use
train_loader = DataLoader(datasets.ImageFolder(train_dir, transform=train_aug),
                          batch_size=train_batch, shuffle=True, num_workers=num_workers, pin_memory=True)
val_target_loader = DataLoader(datasets.ImageFolder(val_target_dir, val_aug),
                       batch_size=test_batch, shuffle=True, num_workers=num_workers, pin_memory=True)
val_source_loader = DataLoader(datasets.ImageFolder(val_source_dir, val_aug),
                       batch_size=test_batch, shuffle=True, num_workers=num_workers, pin_memory=True)

# Model

In [10]:
teacher_model = EfficientNet.from_name(model_name, num_classes=num_classes,
                              override_params={'dropout_rate':0.2, 'drop_connect_rate':0.2})
student_model = EfficientNet.from_name(model_name, num_classes=num_classes,
                              override_params={'dropout_rate':0.8, 'drop_connect_rate':0.5})

# Pre-trained
if pretrained:
    print("=> using pre-trained model '{}'".format(pretrained))
    teacher_model.load_state_dict(torch.load(pretrained)['state_dict'])
    student_model.load_state_dict(torch.load(pretrained)['state_dict'])

=> using pre-trained model './log/pggan/128/b0/aug/checkpoint.pth.tar'


In [11]:
teacher_model.to('cuda')
student_model.to('cuda')
cudnn.benchmark = True
print('    Total params: %.2fM' % (sum(p.numel() for p in teacher_model.parameters())/1000000.0))

    Total params: 4.01M


# Loss

In [12]:
# Resume
if resume:
    print('==> Resuming from checkpoint..')
    checkpoint = os.path.dirname(resume)
#     checkpoint = torch.load(resume)
    resume = torch.load(resume)
    best_acc = resume['best_acc']
    start_epoch = resume['epoch']
    student_model.load_state_dict(resume['state_dict'])
    optimizer.load_state_dict(resume['optimizer'])
    logger = Logger(os.path.join(checkpoint, 'log.txt'), resume=True)
else:
    logger = Logger(os.path.join(checkpoint, 'log.txt'))
    logger.set_names(['Learning Rate', 'Train Loss', 'Valid Loss', 'Source Loss', 'Train Acc.', 'Valid Acc.', 'Source ACC.', 'Train AUROC', 'Valid AUROC', 'Source AUROC'])

In [13]:
for param in teacher_model.parameters():
    param.requires_grad = False
teacher_model.eval()

EfficientNet(
  (_conv_stem): Conv2dStaticSamePadding(
    3, 32, kernel_size=(3, 3), stride=(2, 2), bias=False
    (static_padding): ZeroPad2d(padding=(0, 1, 0, 1), value=0.0)
  )
  (_gn0): GroupNorm(8, 32, eps=1e-05, affine=True)
  (_blocks): ModuleList(
    (0): MBConvBlock(
      (_depthwise_conv): Conv2dStaticSamePadding(
        32, 32, kernel_size=(3, 3), stride=[1, 1], groups=32, bias=False
        (static_padding): ZeroPad2d(padding=(1, 1, 1, 1), value=0.0)
      )
      (_gn1): GroupNorm(8, 32, eps=1e-05, affine=True)
      (_se_reduce): Conv2dStaticSamePadding(
        32, 8, kernel_size=(1, 1), stride=(1, 1)
        (static_padding): Identity()
      )
      (_se_expand): Conv2dStaticSamePadding(
        8, 32, kernel_size=(1, 1), stride=(1, 1)
        (static_padding): Identity()
      )
      (_project_conv): Conv2dStaticSamePadding(
        32, 16, kernel_size=(1, 1), stride=(1, 1), bias=False
        (static_padding): Identity()
      )
      (_gn2): GroupNorm(8, 16, ep

In [14]:
teacher_model_weights = {}
for name, param in teacher_model.named_parameters():
    teacher_model_weights[name] = param.detach()

In [15]:
def reg_cls(model):
    l2_cls = torch.tensor(0.).cuda()
    for name, param in model.named_parameters():
        if name.startswith(fc_name):
            l2_cls += 0.5 * torch.norm(param) ** 2
    return l2_cls

def reg_l2sp(model):
    sp_loss = torch.tensor(0.).cuda()
    for name, param in model.named_parameters():
        if not name.startswith(fc_name):
            sp_loss += 0.5 * torch.norm(param - teacher_model_weights[name]) ** 2
    return sp_loss

In [16]:
criterion = nn.CrossEntropyLoss().cuda()
optimizer = optim.SGD(student_model.parameters(), lr=lr, momentum=momentum)
# optimizer = optim.Adam(student_model.parameters())
scheduler_cosine = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, epochs)
scheduler_warmup = GradualWarmupScheduler(optimizer, multiplier=8, total_epoch=10, after_scheduler=scheduler_cosine)

# Train

In [17]:
def train(train_loader, model, criterion, optimizer, epoch, use_cuda):
    model.train()
    
    batch_time = AverageMeter()
    data_time = AverageMeter()
    losses = AverageMeter()
    top1 = AverageMeter()
    arc = AverageMeter()
    end = time.time()
    cls_losses = AverageMeter()
    sp_losses = AverageMeter()
    main_losses = AverageMeter()
    
    for batch_idx, (inputs, targets) in enumerate(train_loader):
        batch_size = inputs.size(0)
        if batch_size < train_batch:
            continue
        # measure data loading time
        data_time.update(time.time() - end)

        if use_cuda:
            inputs, targets = inputs.cuda(), targets.cuda()
            
        r = np.random.rand(1)
        if cm_beta > 0 and r < cm_prob:
            
            rand_index = torch.randperm(inputs.size()[0]).cuda()
            tt= targets[rand_index]
            boolean = targets==tt
            rand_index = rand_index[boolean]
            lam = np.random.beta(cm_beta, cm_beta)
            bbx1, bby1, bbx2, bby2 = rand_bbox(inputs.size(), lam)
            inputs[boolean, :, bbx1:bbx2, bby1:bby2] = inputs[rand_index, :, bbx1:bbx2, bby1:bby2]

        # compute output
        outputs = model(inputs)
        loss_main = criterion(outputs, targets)
        loss_cls = 0
        loss_sp = 0
        loss_cls = reg_cls(model)
        loss_sp = reg_l2sp(model)
        loss =  loss_main + sp_alpha*loss_sp + sp_beta*loss_cls

        # measure accuracy and record loss
        prec1 = accuracy(outputs.data, targets.data)
        auroc = roc_auc_score(targets.cpu().detach().numpy(), outputs.cpu().detach().numpy()[:,1])
        losses.update(loss.data.tolist(), inputs.size(0))
        top1.update(prec1[0], inputs.size(0))
        arc.update(auroc, inputs.size(0))
        cls_losses.update(loss_cls, inputs.size(0))
        sp_losses.update(loss_sp, inputs.size(0))
        main_losses.update(loss_main.tolist(), inputs.size(0))

        # compute gradient and do SGD step
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        # measure elapsed time
        batch_time.update(time.time() - end)
        end = time.time()
        
        if batch_idx % 100 == 0:
            print('{batch}/{size} | Loss:{loss:.4f} | MainLoss:{main:.4f} | SPLoss:{sp:.4f} | CLSLoss:{cls:.4f} | top1:{tp1:.4f} | AUROC:{ac:.4f}'.format(
                     batch=batch_idx+1, size=len(train_loader), loss=losses.avg, main=main_losses.avg, sp=sp_losses.avg, cls=cls_losses.avg, tp1=top1.avg, ac=arc.avg))
    print('{batch}/{size} | Loss:{loss:.4f} | MainLoss:{main:.4f} | SPLoss:{sp:.4f} | CLSLoss:{cls:.4f} | top1:{tp1:.4f} | AUROC:{ac:.4f}'.format(
                     batch=batch_idx+1, size=len(train_loader), loss=losses.avg, main=main_losses.avg, sp=sp_losses.avg, cls=cls_losses.avg, tp1=top1.avg, ac=arc.avg))
    return (losses.avg, top1.avg, arc.avg)

In [18]:
def test(val_loader, model, criterion, epoch, use_cuda):
    global best_acc

    batch_time = AverageMeter()
    data_time = AverageMeter()
    losses = AverageMeter()
    top1 = AverageMeter()
    arc = AverageMeter()
    cls_losses = AverageMeter()
    sp_losses = AverageMeter()
    main_losses = AverageMeter()


    # switch to evaluate mode
    model.eval()

    end = time.time()
    with torch.no_grad():
        for batch_idx, (inputs, targets) in enumerate(val_loader):
            # measure data loading time
            data_time.update(time.time() - end)

            if use_cuda:
                inputs, targets = inputs.cuda(), targets.cuda()

            # compute output
            outputs = model(inputs)
            loss_main = criterion(outputs, targets)
            loss_cls = 0
            loss_sp = 0
            loss_cls = reg_cls(model)
            loss_sp = reg_l2sp(model)
            loss = loss_main + sp_alpha*loss_sp + sp_beta*loss_cls

            # measure accuracy and record loss
            prec1 = accuracy(outputs.data, targets.data)
            auroc = roc_auc_score(targets.cpu().detach().numpy(), outputs.cpu().detach().numpy()[:,1])
            losses.update(loss.data.tolist(), inputs.size(0))
            top1.update(prec1[0], inputs.size(0))
            arc.update(auroc, inputs.size(0))
            cls_losses.update(loss_cls, inputs.size(0))
            sp_losses.update(loss_sp, inputs.size(0))
            main_losses.update(loss_main.tolist(), inputs.size(0))


            # measure elapsed time
            batch_time.update(time.time() - end)
            end = time.time()

    print('{batch}/{size} | Loss:{loss:.4f} | MainLoss:{main:.4f} | SPLoss:{sp:.4f} | CLSLoss:{cls:.4f} | top1:{tp1:.4f} | AUROC:{ac:.4f}'.format(
                     batch=batch_idx+1, size=len(train_loader), loss=losses.avg, main=main_losses.avg, sp=sp_losses.avg, cls=cls_losses.avg, tp1=top1.avg, ac=arc.avg))
    return (losses.avg, top1.avg, arc.avg)

In [19]:
def save_checkpoint(state, is_best, checkpoint='checkpoint', filename='checkpoint.pth.tar'):
    filepath = os.path.join(checkpoint, filename)
    torch.save(state, filepath)
    if is_best:
        shutil.copyfile(filepath, os.path.join(checkpoint, 'model_best.pth.tar'))

def adjust_learning_rate(optimizer, epoch):
    global state
    lr_set = [1, 1e-1, 1e-2, 1e-3, 1e-4, 1e-5]
    lr_list = schedule.copy()
    lr_list.append(epoch)
    lr_list.sort()
    idx = lr_list.index(epoch)
    state['lr'] *= lr_set[idx]
    for param_group in optimizer.param_groups:
        param_group['lr'] = state['lr']

In [ ]:
for epoch in range(start_epoch, epochs):
    state['lr'] = optimizer.state_dict()['param_groups'][0]['lr']
    adjust_learning_rate(optimizer, epoch)
    print('\nEpoch: [%d | %d] LR: %f' % (epoch + 1, epochs, state['lr']))
    
    train_loss, train_acc, train_auroc = train(train_loader, student_model, criterion, optimizer, epoch, use_cuda)
    if epoch % 20 == 0:
        test_loss, test_acc, test_auroc = test(val_target_loader, student_model, criterion, epoch, use_cuda)
        source_loss, source_acc, source_auroc = test(val_source_loader, student_model, criterion, epoch, use_cuda)

    
        logger.append([state['lr'], train_loss, test_loss,  source_loss, train_acc, test_acc,source_acc, train_auroc, test_auroc, source_auroc])
        is_best = test_acc > best_acc
        best_acc = max(test_acc, best_acc)
        save_checkpoint({
            'epoch': epoch + 1,
            'state_dict' : teacher_model.state_dict(),
            'acc': test_acc,
            'best_acc': best_acc,
            'optimizer': optimizer.state_dict(),
        }, is_best, checkpoint=checkpoint)
    scheduler_warmup.step()


Epoch: [1 | 40000] LR: 0.040000
1/4 | Loss:1.7840 | MainLoss:1.5906 | SPLoss:0.0000 | CLSLoss:1.9344 | top1:71.0000 | AUROC:0.7719
4/4 | Loss:0.9818 | MainLoss:0.7892 | SPLoss:0.0636 | CLSLoss:1.8624 | top1:71.5000 | AUROC:0.8112
39/4 | Loss:0.9767 | MainLoss:0.7876 | SPLoss:0.0895 | CLSLoss:1.8022 | top1:48.7308 | AUROC:0.4795
161/4 | Loss:0.2203 | MainLoss:0.0312 | SPLoss:0.0895 | CLSLoss:1.8022 | top1:99.6355 | AUROC:1.0000

Epoch: [2 | 40000] LR: 0.068000
1/4 | Loss:0.6506 | MainLoss:0.4614 | SPLoss:0.0895 | CLSLoss:1.8022 | top1:75.0000 | AUROC:0.8525
4/4 | Loss:0.6339 | MainLoss:0.4481 | SPLoss:0.0925 | CLSLoss:1.7658 | top1:76.0000 | AUROC:0.8598

Epoch: [3 | 40000] LR: 0.096000
1/4 | Loss:0.5912 | MainLoss:0.4113 | SPLoss:0.0924 | CLSLoss:1.7064 | top1:74.0000 | AUROC:0.8726
4/4 | Loss:0.6207 | MainLoss:0.4448 | SPLoss:0.1017 | CLSLoss:1.6575 | top1:74.7500 | AUROC:0.8639

Epoch: [4 | 40000] LR: 0.124000
1/4 | Loss:0.6050 | MainLoss:0.4352 | SPLoss:0.1220 | CLSLoss:1.5762 | to

4/4 | Loss:2.5426 | MainLoss:0.5170 | SPLoss:20.1051 | CLSLoss:0.1518 | top1:72.0000 | AUROC:0.8149

Epoch: [35 | 40000] LR: 0.320000
1/4 | Loss:2.2323 | MainLoss:0.4913 | SPLoss:17.2627 | CLSLoss:0.1468 | top1:77.0000 | AUROC:0.8450
4/4 | Loss:2.0721 | MainLoss:0.4736 | SPLoss:15.8264 | CLSLoss:0.1586 | top1:74.2500 | AUROC:0.8419

Epoch: [36 | 40000] LR: 0.320000
1/4 | Loss:1.9163 | MainLoss:0.5161 | SPLoss:13.8567 | CLSLoss:0.1456 | top1:66.0000 | AUROC:0.7685
4/4 | Loss:1.7723 | MainLoss:0.4677 | SPLoss:12.8957 | CLSLoss:0.1508 | top1:72.2500 | AUROC:0.8355

Epoch: [37 | 40000] LR: 0.320000
1/4 | Loss:1.7540 | MainLoss:0.4644 | SPLoss:12.7458 | CLSLoss:0.1503 | top1:76.0000 | AUROC:0.8379
4/4 | Loss:2.8625 | MainLoss:0.5550 | SPLoss:22.9381 | CLSLoss:0.1370 | top1:66.2500 | AUROC:0.7970

Epoch: [38 | 40000] LR: 0.320000
1/4 | Loss:6.7383 | MainLoss:0.4487 | SPLoss:62.7759 | CLSLoss:0.1195 | top1:75.0000 | AUROC:0.8483
4/4 | Loss:6.8849 | MainLoss:0.4955 | SPLoss:63.7704 | CLSLoss:0

1/4 | Loss:3.9920 | MainLoss:0.6146 | SPLoss:33.6500 | CLSLoss:0.1234 | top1:58.0000 | AUROC:0.6461
4/4 | Loss:3.6291 | MainLoss:0.5520 | SPLoss:30.6439 | CLSLoss:0.1270 | top1:65.7500 | AUROC:0.7784

Epoch: [69 | 40000] LR: 0.319998
1/4 | Loss:3.1374 | MainLoss:0.5152 | SPLoss:26.0833 | CLSLoss:0.1390 | top1:66.0000 | AUROC:0.8189
4/4 | Loss:2.8758 | MainLoss:0.4804 | SPLoss:23.8092 | CLSLoss:0.1444 | top1:71.2500 | AUROC:0.8545

Epoch: [70 | 40000] LR: 0.319998
1/4 | Loss:2.5949 | MainLoss:0.4546 | SPLoss:21.2540 | CLSLoss:0.1497 | top1:75.0000 | AUROC:0.8622
4/4 | Loss:2.4681 | MainLoss:0.4974 | SPLoss:19.5457 | CLSLoss:0.1609 | top1:73.5000 | AUROC:0.8301

Epoch: [71 | 40000] LR: 0.319998
1/4 | Loss:5.4257 | MainLoss:0.5903 | SPLoss:48.2103 | CLSLoss:0.1435 | top1:62.0000 | AUROC:0.8101
4/4 | Loss:4.9428 | MainLoss:0.5298 | SPLoss:43.9967 | CLSLoss:0.1337 | top1:68.2500 | AUROC:0.8295

Epoch: [72 | 40000] LR: 0.319998
1/4 | Loss:4.5175 | MainLoss:0.3757 | SPLoss:41.2719 | CLSLoss:0

161/4 | Loss:1.3452 | MainLoss:0.0576 | SPLoss:12.6888 | CLSLoss:0.1872 | top1:98.8318 | AUROC:0.9997

Epoch: [102 | 40000] LR: 0.032000
1/4 | Loss:1.7131 | MainLoss:0.4255 | SPLoss:12.6888 | CLSLoss:0.1872 | top1:74.0000 | AUROC:0.8474
4/4 | Loss:1.6931 | MainLoss:0.4172 | SPLoss:12.5720 | CLSLoss:0.1874 | top1:74.0000 | AUROC:0.8550

Epoch: [103 | 40000] LR: 0.032000
1/4 | Loss:1.6292 | MainLoss:0.3723 | SPLoss:12.3811 | CLSLoss:0.1879 | top1:82.0000 | AUROC:0.9176
4/4 | Loss:1.6384 | MainLoss:0.3929 | SPLoss:12.2660 | CLSLoss:0.1895 | top1:78.0000 | AUROC:0.8961

Epoch: [104 | 40000] LR: 0.032000
1/4 | Loss:1.6460 | MainLoss:0.4195 | SPLoss:12.0764 | CLSLoss:0.1885 | top1:71.0000 | AUROC:0.8458
4/4 | Loss:1.6258 | MainLoss:0.4105 | SPLoss:11.9639 | CLSLoss:0.1883 | top1:74.7500 | AUROC:0.8666

Epoch: [105 | 40000] LR: 0.032000
1/4 | Loss:1.6243 | MainLoss:0.4273 | SPLoss:11.7807 | CLSLoss:0.1890 | top1:70.0000 | AUROC:0.8271
4/4 | Loss:1.6027 | MainLoss:0.4165 | SPLoss:11.6736 | CLS

1/4 | Loss:1.0118 | MainLoss:0.4330 | SPLoss:5.5953 | CLSLoss:0.1930 | top1:71.0000 | AUROC:0.8576
4/4 | Loss:0.9822 | MainLoss:0.4081 | SPLoss:5.5480 | CLSLoss:0.1928 | top1:73.2500 | AUROC:0.8644

Epoch: [137 | 40000] LR: 0.031999
1/4 | Loss:0.9604 | MainLoss:0.3945 | SPLoss:5.4652 | CLSLoss:0.1939 | top1:77.0000 | AUROC:0.8889
4/4 | Loss:0.9614 | MainLoss:0.4004 | SPLoss:5.4172 | CLSLoss:0.1932 | top1:74.7500 | AUROC:0.8684

Epoch: [138 | 40000] LR: 0.031999
1/4 | Loss:0.9052 | MainLoss:0.3524 | SPLoss:5.3356 | CLSLoss:0.1930 | top1:77.0000 | AUROC:0.9180
4/4 | Loss:0.9515 | MainLoss:0.4033 | SPLoss:5.2879 | CLSLoss:0.1941 | top1:77.2500 | AUROC:0.8903

Epoch: [139 | 40000] LR: 0.031999
1/4 | Loss:0.9032 | MainLoss:0.3625 | SPLoss:5.2125 | CLSLoss:0.1944 | top1:84.0000 | AUROC:0.9348
4/4 | Loss:0.9180 | MainLoss:0.3820 | SPLoss:5.1641 | CLSLoss:0.1955 | top1:80.0000 | AUROC:0.9046

Epoch: [140 | 40000] LR: 0.031999
1/4 | Loss:0.9067 | MainLoss:0.3786 | SPLoss:5.0850 | CLSLoss:0.1962

...

1/4 | Loss:0.4142 | MainLoss:0.3691 | SPLoss:0.2497 | CLSLoss:0.2019 | top1:75.0000 | AUROC:0.8976
4/4 | Loss:0.4016 | MainLoss:0.3565 | SPLoss:0.2497 | CLSLoss:0.2019 | top1:80.7500 | AUROC:0.9094
39/4 | Loss:0.7864 | MainLoss:0.7412 | SPLoss:0.2497 | CLSLoss:0.2019 | top1:48.7692 | AUROC:0.4770
161/4 | Loss:0.0766 | MainLoss:0.0314 | SPLoss:0.2497 | CLSLoss:0.2019 | top1:99.4268 | AUROC:0.9998

Epoch: [17382 | 40000] LR: 0.000193
1/4 | Loss:0.4033 | MainLoss:0.3581 | SPLoss:0.2497 | CLSLoss:0.2019 | top1:79.0000 | AUROC:0.9000
4/4 | Loss:0.4021 | MainLoss:0.3569 | SPLoss:0.2496 | CLSLoss:0.2019 | top1:77.7500 | AUROC:0.9006

Epoch: [17383 | 40000] LR: 0.000193
1/4 | Loss:0.4000 | MainLoss:0.3548 | SPLoss:0.2496 | CLSLoss:0.2019 | top1:85.0000 | AUROC:0.9307
4/4 | Loss:0.4252 | MainLoss:0.3801 | SPLoss:0.2496 | CLSLoss:0.2019 | top1:81.0000 | AUROC:0.9050

Epoch: [17384 | 40000] LR: 0.000193
1/4 | Loss:0.4042 | MainLoss:0.3590 | SPLoss:0.2496 | CLSLoss:0.2019 | top1:79.0000 | AUROC:0.

4/4 | Loss:0.4122 | MainLoss:0.3671 | SPLoss:0.2493 | CLSLoss:0.2019 | top1:79.2500 | AUROC:0.8993

Epoch: [17415 | 40000] LR: 0.000192
1/4 | Loss:0.3906 | MainLoss:0.3455 | SPLoss:0.2492 | CLSLoss:0.2019 | top1:79.0000 | AUROC:0.9115
4/4 | Loss:0.3971 | MainLoss:0.3520 | SPLoss:0.2492 | CLSLoss:0.2019 | top1:80.5000 | AUROC:0.9120

Epoch: [17416 | 40000] LR: 0.000192
1/4 | Loss:0.3562 | MainLoss:0.3111 | SPLoss:0.2492 | CLSLoss:0.2019 | top1:85.0000 | AUROC:0.9261
4/4 | Loss:0.4162 | MainLoss:0.3711 | SPLoss:0.2492 | CLSLoss:0.2019 | top1:78.2500 | AUROC:0.8895

Epoch: [17417 | 40000] LR: 0.000192
1/4 | Loss:0.4241 | MainLoss:0.3789 | SPLoss:0.2492 | CLSLoss:0.2018 | top1:79.0000 | AUROC:0.9093
4/4 | Loss:0.3809 | MainLoss:0.3358 | SPLoss:0.2492 | CLSLoss:0.2019 | top1:82.5000 | AUROC:0.9275

Epoch: [17418 | 40000] LR: 0.000192
1/4 | Loss:0.3830 | MainLoss:0.3379 | SPLoss:0.2492 | CLSLoss:0.2019 | top1:83.0000 | AUROC:0.9177
4/4 | Loss:0.4006 | MainLoss:0.3555 | SPLoss:0.2492 | CLSLos

1/4 | Loss:0.3860 | MainLoss:0.3409 | SPLoss:0.2490 | CLSLoss:0.2019 | top1:77.0000 | AUROC:0.8968
4/4 | Loss:0.3803 | MainLoss:0.3352 | SPLoss:0.2490 | CLSLoss:0.2019 | top1:79.7500 | AUROC:0.9100

Epoch: [17449 | 40000] LR: 0.000192
1/4 | Loss:0.3514 | MainLoss:0.3064 | SPLoss:0.2489 | CLSLoss:0.2019 | top1:86.0000 | AUROC:0.9568
4/4 | Loss:0.3931 | MainLoss:0.3480 | SPLoss:0.2489 | CLSLoss:0.2019 | top1:80.2500 | AUROC:0.9185

Epoch: [17450 | 40000] LR: 0.000192
1/4 | Loss:0.3853 | MainLoss:0.3402 | SPLoss:0.2489 | CLSLoss:0.2019 | top1:81.0000 | AUROC:0.9225
4/4 | Loss:0.4025 | MainLoss:0.3574 | SPLoss:0.2489 | CLSLoss:0.2019 | top1:80.7500 | AUROC:0.9120

Epoch: [17451 | 40000] LR: 0.000192
1/4 | Loss:0.3771 | MainLoss:0.3320 | SPLoss:0.2489 | CLSLoss:0.2019 | top1:84.0000 | AUROC:0.9304
4/4 | Loss:0.3872 | MainLoss:0.3422 | SPLoss:0.2489 | CLSLoss:0.2019 | top1:81.2500 | AUROC:0.9225

Epoch: [17452 | 40000] LR: 0.000192
1/4 | Loss:0.4001 | MainLoss:0.3551 | SPLoss:0.2488 | CLSLos

161/4 | Loss:0.0825 | MainLoss:0.0374 | SPLoss:0.2485 | CLSLoss:0.2019 | top1:99.3084 | AUROC:0.9996

Epoch: [17482 | 40000] LR: 0.000192
1/4 | Loss:0.4004 | MainLoss:0.3553 | SPLoss:0.2485 | CLSLoss:0.2019 | top1:76.0000 | AUROC:0.9028
4/4 | Loss:0.3917 | MainLoss:0.3467 | SPLoss:0.2485 | CLSLoss:0.2020 | top1:82.5000 | AUROC:0.9189

Epoch: [17483 | 40000] LR: 0.000192
1/4 | Loss:0.3492 | MainLoss:0.3042 | SPLoss:0.2485 | CLSLoss:0.2020 | top1:84.0000 | AUROC:0.9587
4/4 | Loss:0.4024 | MainLoss:0.3574 | SPLoss:0.2485 | CLSLoss:0.2020 | top1:78.2500 | AUROC:0.9038

Epoch: [17484 | 40000] LR: 0.000192
1/4 | Loss:0.4395 | MainLoss:0.3944 | SPLoss:0.2485 | CLSLoss:0.2020 | top1:76.0000 | AUROC:0.8768
4/4 | Loss:0.3840 | MainLoss:0.3389 | SPLoss:0.2485 | CLSLoss:0.2020 | top1:81.7500 | AUROC:0.9272

Epoch: [17485 | 40000] LR: 0.000192
1/4 | Loss:0.3970 | MainLoss:0.3519 | SPLoss:0.2485 | CLSLoss:0.2020 | top1:82.0000 | AUROC:0.9106
4/4 | Loss:0.4312 | MainLoss:0.3861 | SPLoss:0.2485 | CLSL

4/4 | Loss:0.4175 | MainLoss:0.3725 | SPLoss:0.2483 | CLSLoss:0.2020 | top1:77.7500 | AUROC:0.9053

Epoch: [17516 | 40000] LR: 0.000191
1/4 | Loss:0.3735 | MainLoss:0.3284 | SPLoss:0.2483 | CLSLoss:0.2020 | top1:78.0000 | AUROC:0.9105
4/4 | Loss:0.3911 | MainLoss:0.3460 | SPLoss:0.2483 | CLSLoss:0.2020 | top1:80.5000 | AUROC:0.9136

Epoch: [17517 | 40000] LR: 0.000191
1/4 | Loss:0.3902 | MainLoss:0.3452 | SPLoss:0.2483 | CLSLoss:0.2020 | top1:79.0000 | AUROC:0.9062
4/4 | Loss:0.3868 | MainLoss:0.3417 | SPLoss:0.2483 | CLSLoss:0.2020 | top1:82.7500 | AUROC:0.9195

Epoch: [17518 | 40000] LR: 0.000191
1/4 | Loss:0.4468 | MainLoss:0.4018 | SPLoss:0.2483 | CLSLoss:0.2020 | top1:77.0000 | AUROC:0.8709
4/4 | Loss:0.3902 | MainLoss:0.3452 | SPLoss:0.2483 | CLSLoss:0.2020 | top1:79.2500 | AUROC:0.9069

Epoch: [17519 | 40000] LR: 0.000191
1/4 | Loss:0.3845 | MainLoss:0.3395 | SPLoss:0.2483 | CLSLoss:0.2020 | top1:80.0000 | AUROC:0.9244
4/4 | Loss:0.4052 | MainLoss:0.3602 | SPLoss:0.2483 | CLSLos